# CS 201: Recursion
<p>
<script language="JavaScript">
    document.write("Last modified: " + document.lastModified)
</script>

In [14]:
(require racket)
(require racket/base)

### Recursion, Glorious, Recursion
See <a target=ee href="recursion.rkt">recursion.rkt</a> and try out the trace facility.

modulo vs remainder See <a target=qw href="modulo.rkt">modulo.rkt</a> (Also, quotient vs /)

Recursive procedures that take lists as arguments and return lists as values.

See <a target=wer href="racket4.rkt">racket4.rkt</a>

Recall from above that we have list predicates: <tt>empty?, null?, list?</tt>, list selectors: <tt>first, rest, car, cdr</tt>, and a list constructor: <tt>cons</tt>.

There is a built-in procedure <code>(length lst)</code> that takes a list <tt>lst</tt> as its argument and returns the number of top-level elements in lst. For example we have the following.

In [15]:
(length '())

0

In [16]:
(length '(a b c))

3

In [17]:
(length '((1 2) (3 4 5)))

2

We'll write our own recursive version of length, <code>(our-length lst)</code>. As we saw, we need one or more base cases. A natural one for an input list is the empty list, <tt>'()</tt>. If the input list is empty, we can immediately return the value 0 for <code>our-length</code>. We also need one or more recursive cases that "move" the input towards a base case. In the case of an input list, removing one element from the list (by using <tt>rest</tt> or <tt>cdr</tt>) is a natural candidate, since it moves towards the empty list as a base case. As we think about how to construct the procedure, it may be helpful to consider an example. 

In [18]:
(define lst '(17 24 6))

In [19]:
(rest lst) 

'(24 6)

In [20]:
(length (rest lst))

2

In [21]:
(first lst)

17

In [22]:
(length lst)

3

In this case, if the recursive call <code>(our-length (rest lst)</code>) returns a correct value, we just need to add 1 to it to get a correct answer for <code>(our-length lst)</code>. We don't actually seem to need the value of <code>(first lst)</code> at all. We are led to define the following procedure.

In [23]:
(define (our-length lst)
  (if (empty? lst)
      0
      (+ 1 (our-length (rest lst)))))

We can draw a tree of the recursive calls of <code>(our-length '(17 24 6))</code> to help us understand how this works.
<pre>
    (our-length '(17 24 6))
     /  |     \
    +   1   (our-length '(24 6))
             /  |     \
            +   1    (our-length '(6))
                      /  |     \
                     +   1    (our-length '())
</pre>


Notice that each successive recursive call has an argument that is one element shorter than its predecessor, until we reach the base case of the empty list <tt>'()</tt>. Then there is no further recursive call, and the procedure just returns 0, leading to the following sequence of return values (from the bottom up.)

<pre>
    (our-length '(17 24 6)) => 3
     /  |     \
    +   1   (our-length '(24 6)) => 2
             /  |     \
            +   1    (our-length '(6)) => 1
                      /  |     \
                     +   1    (our-length '()) => 0

</pre>

Note that the <tt>if</tt> expression tests <code>(empty? lst)</code> -- it would be equivalent to test <code>(null? lst)</code> or <code>(equal? lst '())</code>.

This procedure is not tail-recursive, because the value of the recursive call, (<code>our-length (rest lst))</code> is modified, that is, has 1 added to it, before being returned as the value of <code>(our-length lst)</code>.  We discuss tail-recursion below.

In [24]:
(our-length '(17 24 6))

3

In [25]:
(require racket/trace)

In [26]:
(trace our-length)

In [27]:
(our-length '(17 24 6))

>(our-length '(17 24 6))
> (our-length '(24 6))
> >(our-length '(6))
> > (our-length '())
< < 0
< <1
< 2
<3


3

### Testing whether an element is in a list.
There is a built-in procedure <code>(member item lst)</code> to test whether an arbitrary item is <tt>equal?</tt> to a top-level element of the list <tt>lst</tt>. If item is not <tt>equal?</tt> to any of the top-level elements of <tt>lst</tt>, then this procedure returns #f. If item is equal to some top-level element of lst, then this procedure returns a list with all the remaining elements of lst from the first one <tt>equal?</tt> to item until the end. As examples, we have the following.

In [28]:
(member 2 '(1 2 3))

'(2 3)

In [29]:
(member 2 '(1 2 3 2 1)) 

'(2 3 2 1)

In [30]:
(member 4 '(1 2 3)) 

#f

Note that this is not a predicate, because it does not always return <tt>#t</tt> or <tt>#f</tt>. We'll write (as a recursive procedure) a predicate version of <tt>member</tt>, namely <code>(member? item lst)</code>. If item is <tt>equal?</tt> to a top-level element of <tt>lst</tt>, then <code>(member? item lst)</code> evaluates to <tt>#t</tt>; otherwise, it evaluates to <tt>#f</tt> We can define a trivial version using <tt>member</tt>.

In [31]:
(define (member? item lst)
  (if (member item lst) #t #f))

In [32]:
(member? 2 '(1 2 3)) 

#t

In [33]:
(member? 2 '(1 2 3 2 1))

#t

In [34]:
(member? 4 '(1 2 3)) 

#f

Because the input <tt>lst</tt> is a list, a reasonable base case is when <tt>lst</tt> is an empty list. In this case, lst contains no top-level elements, so item cannot be <tt>equal?</tt> to one of them, and the procedure should return <tt>#f</tt>. Thinking about the first example above, we have <code>item => 2</code> and <code>lst => '(1 2 3)</code>.

<pre>
    (first lst) => 1
    (rest lst) => '(2 3)
    (member? item (rest lst)) => #t   (if it returns the correct answer)
</pre>

So there should be a recursive case in which we evaluate <code>(member? item (rest lst))</code> and return the value that it returns. However, this isn't the only case; we have the case in which item is actually <tt>equal?</tt> to <code>(first lst)</code>. This is another base case, which should return the value <tt>#t</tt>. We are led to the following procedure definition.

In [35]:
(define (member? item lst)
      (cond
        [(empty? lst) #f]
        [(equal? item (first lst)) #t]
        [else (member? item (rest lst))]))

In [36]:
(define (ifmember? item lst)
  (if (empty? lst) #f
      (if (equal? item (first lst))
          #t
          (ifmember? item (rest lst)))))

In [37]:
(ifmember? 2 '(1 2 3))

#t


We used a <tt>cond</tt> special form to avoid a situation of nested if expressions. There are two base cases: <tt>lst</tt> is empty, and the answer is <tt>#f</tt>, and the list is non-empty and item is <tt>equal?</tt> to the first element of <tt>lst</tt>, when the answer is <tt>#t</tt>. If neither of these cases applies, then we need to continue to search for item in the rest of the list. The answer (<tt>#t</tt> or <tt>#f</tt>) that the recursive call returns will be the answer to whether <code>(member? item lst)</code> should be <tt>#t</tt> or <tt>#f</tt>. We can draw the tree of recursive calls for <code>(member? 24 '(17 24 6))</code> as follows.
<pre>
    (member? 24 '(17 24 6))
        |
    (member? 24 '(24 6))
</pre>
There are no further recursive calls because 24 is <tt>equal?</tt> to <code>(first lst) </code>in this case, and <tt>#t</tt> is returned. The return value just propagates upward as follows.
<pre>
    (member? 24 '(17 24 6)) => #t
        |
    (member? 24 '(24 6)) => #t
    </pre>
Note that our <tt>member?</tt> procedure is tail-recursive: the value of the recursive call is returned (unmodified) as the value of the whole procedure.

In [38]:
(not 1)

#f

In [39]:
(not '())

#f

<h3 id="double-each">A procedure that takes a list as input and returns a list.</h3>

Now we write a procedure <code>(double-each lst)</code> that takes a list <tt>lst</tt> of numbers and returns the list consisting of twice each number in the original list. As an example we have the following.
<pre>
    (double-each '(17 24 6)) => '(34 48 12)
</pre>
Once again, the empty list is a reasonable base case. We have to decide what we want <code>(double-each '())</code> to be. We choose the result to be <tt>'()</tt>, which consists of twice each number in <tt>'()</tt>. Thinking about the example, if <code>lst => '(17 24 6)</code>, we have the following.
<pre>
    (first lst) => 17
    (rest lst) => '(24 6)
    (double-each (rest lst)) => '(48 12)  (assuming it works correctly)
</pre>    
For the recursive case, we can call <code>(double-each (rest lst))</code>, and get a list containing twice each of the numbers in the rest of the list. To make this into the desired result, all we have to do is to include twice <code>(first lst)</code> at the front of the list. The list constructor <code>(cons item lst)</code> returns the list <tt>equal?</tt> to lst with item included as the first element. We may now write the complete procedure as follows.

In [40]:
(define (double-each lst)
      (if (null? lst)
          '()
          (cons (* 2 (first lst))
                (double-each (rest lst)))))

In [41]:
(double-each '(a b 3))

*: contract violation
  expected: number?
  given: 'a
  argument position: 2nd
  other arguments...:
   2


In [42]:
(double-each '(1 2 3))

'(2 4 6)

In [43]:
(trace double-each)

In [44]:
(double-each '(17 24 6))

>(double-each '(17 24 6))
> (double-each '(24 6))
> >(double-each '(6))
> > (double-each '())
< < '()
< <'(12)
< '(48 12)
<'(34 48 12)


'(34 48 12)

Note that we could get by with an if expression because there were only two cases: the base case and the recursive case. We can draw the tree of recursive calls for the application <code>(double-each '(17 24 6))</code> as follows.
<pre>
    (double-each '(17 24 6))
     /   |    \
   cons  34  (double-each '(24 6))
              /   |    \
            cons  48  (double-each '(6))
                       /   |    \
                     cons  12  (double-each '())
</pre>
There are no further recursive calls because we reached the base case <code>(lst => '())</code>, which returns <tt>'()</tt>. Then the returns propagate up the tree as follows.<pre>
    (double-each '(17 24 6)) => '(34 48 12)
     /   |    \
   cons  34  (double-each '(24 6)) => '(48 12)
              /   |    \
            cons  48  (double-each '(6)) => '(12)
                       /   |    \
                     cons  12  (double-each '()) => '()
</pre>
Note that this procedure is not tail-recursive, because the value returned by the recursive call is modified (by having twice <code>(first lst)</code> cons'ed on the front) before being returned as the value of the whole procedure.

<h3 id="deep"> Deep recursion.</h3>
See add-tree in <a target=qqw href="racket5.rkt">racket5.rkt</a>

So far we have seen recursion on numbers, from n to n-1, or from n to <code>(quotient n 10)</code>, and "flat" recursion on lists, which processes <code>(first lst)</code> in some way and does a recursive call on (rest lst). Now we'll consider a procedure that does "deep recursion", in which the procedure is called recursively on sublists, and sublists of sublists, and so on. There is a built-in procedure <code>(flatten value</code>). Here are some examples of it.

In [45]:
(require racket)
(require racket/base)

In [46]:
(flatten 17)

'(17)

In [47]:
(flatten '(17 24 6))

'(17 24 6)

In [48]:
(flatten '((1 2) (4 (1 2)) 3))

'(1 2 4 1 2 3)

In [49]:
(flatten '(() ()))

'()

If the argument value is not a list, the return value is a list containing it as the only element. If the argument value is the empty list, the return value is the empty list. However, if the argument value is a non-empty list, the result is obtained by appending the result of flattening <code>(first value)</code> to the result of flattening <code>(rest lst)</code>. We'll write our own version of flatten, <code>(o-f value)</code>.

In [50]:
(define (o-f value)
  (cond
        [(not (list? value)) (list value)]
        [(empty? value) '()]
        [else
          (append (o-f (first value))
                  (o-f (rest value)))]))

Note that here we've used the built-in list constructor <tt>list</tt>. This takes an arbitrary finite number of arguments, evaluates all of them, and makes a list of the values. Thus, <code>(list value)</code> is equivalent to <code>(cons value '())</code>. Note the contrast with quote ('), in the following.

In [51]:
(car '('a 1))

''a

In [52]:
(car (quote ((quote a) 1)))

''a

In [53]:
(list 'a 1)

'(a 1)

In [54]:
(list (+ 1 2) (* 2 3))

'(3 6)

In [55]:
'((+ 1 2) (* 3 6))

'((+ 1 2) (* 3 6))

In [56]:
(quote ((+ 1 2) (* 2 3)))

'((+ 1 2) (* 2 3))

In the case of list, the expressions <code>(+ 1 2)</code> and <code>(* 2 3)</code> are evaluated, and the list of their values returned. In the case of quote ('), evaluation of the sub-expressions of the expression is inhibited, and the value of <code>'((+ 1 2) (* 3 6))</code> is a list containing two lists, the first with the identifier <tt>'+</tt>, the number 1 and the number 2, and the second with the identifier <tt>'*</tt>, the number 3 and the number 6.

We may draw the tree of recursive calls for an application like <code>(o-f '((1 2) 3))</code>. 

In [57]:
(require racket/trace)

In [58]:
(trace o-f)

In [59]:
(o-f '((1 2) 3))

>(o-f '((1 2) 3))
> (o-f '(1 2))
> >(o-f 1)
< <'(1)
> >(o-f '(2))
> > (o-f 2)
< < '(2)
> > (o-f '())
< < '()
< <'(2)
< '(1 2)
> (o-f '(3))
> >(o-f 3)
< <'(3)
> >(o-f '())
< <'()
< '(3)
<'(1 2 3)


'(1 2 3)

<pre>
          (o-f '((1 2) 3))
       _______________________
       /    |                 \
      /     |                  \
     /      |                   \
    /       |                    \ 
append  (o-f '(1 2))              (o-f '(3))
       /    |     \               /    |    \
  append  (o-f 1) (o-f '(2))  append (o-f 3) (o-f '())
                 /    |    \
            append (o-f 2) (o-f '()) 
</pre>

All the leaves are base cases (either the empty list or a non-list value), and they are appended and returned up the tree of recursive calls to yield <code>(o-f '((1 2) 3)) => '(1 2 3)</code>.

Going forward, deep recursion will appear in many guises, to traverse or process more complex recursive data structures. It is your friend. Like it on Facebook. (BTW, Facebook is basically a huge graph which is a mammoth recursive data structure.)

### add-tree deep recursion

We first define a variable with a tree structure.

In [60]:
(define s '((2 3 (4) ((5))) ((4)) (3 4 5)))

In [61]:
(flatten s)

'(2 3 4 5 4 3 4 5)

In [62]:
(apply + (flatten s))

30

Now we define <tt>add-tree</tt> which adds up the elements of the tree using deep recursion which returns a single value.

In [63]:
(define (add-tree lst)
  (cond ((null? lst) 0)
    ((number? lst) lst)
    ((list? lst)
     (+ (add-tree (car lst))
        (add-tree (cdr lst))))
    ))

In [64]:
(add-tree s)

30

In [65]:
(trace add-tree)

In [73]:
(add-tree s)

>(add-tree '((2 3 (4) ((5))) ((4)) (3 4 5)))
> (add-tree '(2 3 (4) ((5))))
> >(add-tree 2)
< <2
> >(add-tree '(3 (4) ((5))))
> > (add-tree 3)
< < 3
> > (add-tree '((4) ((5))))
> > >(add-tree '(4))
> > > (add-tree 4)
< < < 4
> > > (add-tree '())
< < < 0
< < <4
> > >(add-tree '(((5))))
> > > (add-tree '((5)))
> > > >(add-tree '(5))
> > > > (add-tree 5)
< < < < 5
> > > > (add-tree '())
< < < < 0
< < < <5
> > > >(add-tree '())
< < < <0
< < < 5
> > > (add-tree '())
< < < 0
< < <5
< < 9
< <12
< 14
> (add-tree '(((4)) (3 4 5)))
> >(add-tree '((4)))
> > (add-tree '(4))
> > >(add-tree 4)
< < <4
> > >(add-tree '())
< < <0
< < 4
> > (add-tree '())
< < 0
< <4
> >(add-tree '((3 4 5)))
> > (add-tree '(3 4 5))
> > >(add-tree 3)
< < <3
> > >(add-tree '(4 5))
> > > (add-tree 4)
< < < 4
> > > (add-tree '(5))
> > > >(add-tree 5)
< < < <5
> > > >(add-tree '())
< < < <0
< < < 5
< < <9
< < 12
> > (add-tree '())
< < 0
< <12
< 16
<30


30

We next define a deep recursive function which transforms the tree, returning a modified version of the tree.  We assume that the tree contains only numeric leaves.

In [74]:
(define (treeadd1 tree)
  (cond ((null? tree) '())
    ((not (pair? tree))
     (+ 1 tree))
    (else
     (cons (treeadd1 (first tree))
           (treeadd1 (rest tree))))))

In [75]:
(treeadd1 '(1 2 d e))

+: contract violation
  expected: number?
  given: 'd
  argument position: 2nd
  other arguments...:
   1


In [76]:
(treeadd1 s)

'((3 4 (5) ((6))) ((5)) (4 5 6))

In [77]:
(trace treeadd1 )

In [78]:
(treeadd1 s)

>(treeadd1 '((2 3 (4) ((5))) ((4)) (3 4 5)))
> (treeadd1 '(2 3 (4) ((5))))
> >(treeadd1 2)
< <3
> >(treeadd1 '(3 (4) ((5))))
> > (treeadd1 3)
< < 4
> > (treeadd1 '((4) ((5))))
> > >(treeadd1 '(4))
> > > (treeadd1 4)
< < < 5
> > > (treeadd1 '())
< < < '()
< < <'(5)
> > >(treeadd1 '(((5))))
> > > (treeadd1 '((5)))
> > > >(treeadd1 '(5))
> > > > (treeadd1 5)
< < < < 6
> > > > (treeadd1 '())
< < < < '()
< < < <'(6)
> > > >(treeadd1 '())
< < < <'()
< < < '((6))
> > > (treeadd1 '())
< < < '()
< < <'(((6)))
< < '((5) ((6)))
< <'(4 (5) ((6)))
< '(3 4 (5) ((6)))
> (treeadd1 '(((4)) (3 4 5)))
> >(treeadd1 '((4)))
> > (treeadd1 '(4))
> > >(treeadd1 4)
< < <5
> > >(treeadd1 '())
< < <'()
< < '(5)
> > (treeadd1 '())
< < '()
< <'((5))
> >(treeadd1 '((3 4 5)))
> > (treeadd1 '(3 4 5))
> > >(treeadd1 3)
< < <4
> > >(treeadd1 '(4 5))
> > > (treeadd1 4)
< < < 5
> > > (treeadd1 '(5))
> > > >(treeadd1 5)
< < < <6
> > > >(treeadd1 '())
< < < <'()
< < < '(6)
< < <'(5 6)
< < '(4 5 6)
> > (treeadd1 '())
< < '(

'((3 4 (5) ((6))) ((5)) (4 5 6))

Finally, we define <tt>double-tree<tt> which copies a tree, replacing each leaf with twice its value.

In [79]:
;; assuming only numeric leaves to the tree
(define (double-tree tree)
  (cond ((null? tree) '())
    ((not (pair? tree))
     (+ tree tree))
    (else
     (cons (double-tree (car tree))
           (double-tree (cdr tree))))))

In [80]:
(double-tree s)

'((4 6 (8) ((10))) ((8)) (6 8 10))

In [60]:
(trace double-tree)

In [61]:
(double-tree s)

>(double-tree '((2 3 (4) ((5))) ((4)) (3 4 5)))
> (double-tree '(2 3 (4) ((5))))
> >(double-tree 2)
< <4
> >(double-tree '(3 (4) ((5))))
> > (double-tree 3)
< < 6
> > (double-tree '((4) ((5))))
> > >(double-tree '(4))
> > > (double-tree 4)
< < < 8
> > > (double-tree '())
< < < '()
< < <'(8)
> > >(double-tree '(((5))))
> > > (double-tree '((5)))
> > > >(double-tree '(5))
> > > > (double-tree 5)
< < < < 10
> > > > (double-tree '())
< < < < '()
< < < <'(10)
> > > >(double-tree '())
< < < <'()
< < < '((10))
> > > (double-tree '())
< < < '()
< < <'(((10)))
< < '((8) ((10)))
< <'(6 (8) ((10)))
< '(4 6 (8) ((10)))
> (double-tree '(((4)) (3 4 5)))
> >(double-tree '((4)))
> > (double-tree '(4))
> > >(double-tree 4)
< < <8
> > >(double-tree '())
< < <'()
< < '(8)
> > (double-tree '())
< < '()
< <'((8))
> >(double-tree '((3 4 5)))
> > (double-tree '(3 4 5))
> > >(double-tree 3)
< < <6
> > >(double-tree '(4 5))
> > > (double-tree 4)
< < < 8
> > > (double-tree '(5))
> > > >(double-tree 5)
< < < <10

'((4 6 (8) ((10))) ((8)) (6 8 10))

In [63]:
(pair? (cons 1 2))

#t

In [64]:
(cons 1 2)

'(1 . 2)

In [65]:
(list? (cons 1 2))

#f

In [66]:
(list? (cons 1 (cons 2 empty)))

#t

In [67]:
empty

'()